<a href="https://colab.research.google.com/github/Legodark/paddok/blob/import_colab/notebooks/machine_learning/PADDOK_MachineLearning.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

### Importación de librerias y paquetes

In [1]:
!pip install tensorflow_decision_forests --upgrade > /dev/null

In [101]:
import time

# Tratamiento de lo datos
import numpy as np
import pandas as pd

# Barra de progreso para los bucles
from tqdm.notebook import tqdm

# Visualización
import plotly
import plotly.express as px
import plotly.graph_objects as go
import matplotlib.pyplot as plt
import seaborn as sns
import scipy.stats as stats

# Machine Learning
# TensorFlow
import tensorflow as tf
from tensorflow import keras
import tensorflow_decision_forests as tfdf
from tensorflow.keras.models import load_model

#Skelearn
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error, r2_score, mean_absolute_error
from sklearn.ensemble import RandomForestRegressor

# Exportación e importación de modelos
import joblib

%matplotlib inline

Versión de Tensorflow

In [3]:
print(tf.__version__)

2.11.0


Establezco el tema de plotly en modo oscuro

In [4]:
plotly.io.templates.default = "plotly_dark"

### Carga del dataset

In [5]:
file_path = '/content/drive/MyDrive/Colab Notebooks/Curso_IA_BIGDATA/TFM/DataSet/DataSet_Visualizacion/cars_to_visualization.csv'

In [6]:
cars = pd.read_csv(file_path)

En este apartado vamos a realizar lo siguiente:

1. Pasar las columnas a nombres en ingles, esto es importante puesto que letras como la ñ pueden provocar errores en los algoritmos de TensorFlow.

2. Eliminar columnas no relevantes, revisando con las correlaciones, por ejemplo, para pasarlos a los algoritmos de TensorFlow debo de eliminar las columnas numericas de las ids, para que no haya datos redundantes.

3. Preparar el datasets de diferentes maneras para pasarselo a los algoritmos de ML.

Esta preparación se va a hacer concretamente para 3 algoritmos (2 de TensorFlow y 1 de Sklearn), y hay que prepararlos de diferente forma, ya que para TensorFlow podemos pasarle valores categorios y numericos, pero para Sklean solo podemos pasar numerios.

Dicho lo anterior voy a preparar el dataset que creamos en el punto 3 Limpieza de datos (Preprocesado) tanto para TensorFlow como para Sklearn.

Los datasets a preparar son los siguientes:

Dataset completo

Dataset limitando el precio y los kilometros

Dataset limitando el precio, los kilometros y las marcas con coches con cantidad inferior a 10

Dataset limitando el precio, los kilometros, las marcas con coches con cantidad inferior a 10 y dejando solo mas columas de mark, model, year, horses, km, fuel, gearbox, price, displacement_engine, marches

Gracias a que pase variables categoricas a numéricas, como, marca, modelo, cambio, combustiable, a la hora de tratar los datasets para Sklearn será mas rápido.

Creo una función para crear correlaciones mas rapidamente.

In [7]:
def correlations(data_corr):
  corr_gen = go.Figure()
  corr_gen.add_trace(
      go.Heatmap(
          x = data_corr.columns,
          y = data_corr.index,
          z = np.array(data_corr),
          text=data_corr.values,
          texttemplate='%{text:.2f}',
          colorscale=[[0, 'green'], [0.5, 'yellow'], [1, 'red']]
      )
  )
  corr_gen.show()

Miro las correlaciones de cars

In [8]:
cars_correlations = cars.corr()

In [9]:
correlations(cars_correlations)

Antes de entrar de lleno en los DataFrame y el Machine Learning voy a cambiar el nombre a las columnas de este para no tener problemas de caracteres mas adelante.

In [10]:
# Muestro una linea para ver el nombre de las columna de forma comoda
cars.head(1)

Unnamed: 0 localidad    marca               modelo     año  motor (CV)  \
0           0    Madrid  Citroen  Citroen C3 aircross  2022.0       110.0   

   motor (KW)  kilometros combustible  cambio  ...  plazas  deposito  \
0        81.0      7119.0    Gasolina  Manual  ...     5.0      45.0   

   0-100 km/h  cilindrada  marchas  marca_id  modelo_id  combustible_id  \
0         8.8      1199.0      6.0      10.0      118.0             3.0   

   cambio_id  localidad_id  
0        1.0          28.0  

[1 rows x 22 columns]

Cambio el nombre de las columnas

In [11]:
cars = cars.rename(columns={'Unnamed: 0': 'id_car', 'localidad': 'locate', 'marca': 'car_brand', 'modelo': 'model', 'año': 'year', 'motor (CV)': 'horses', 'motor (KW)': 'engine_power', 'kilometros': 'km', 'combustible': 'fuel', 'cambio': 'gearbox', 'emisiones': 'CO2', 'precio': 'price', 'plazas': 'places', 'deposito': 'deposit', '0-100 km/h': '0_100km', 'cilindrada': 'displ_engine', 'marchas': 'marches', 'marca_id': 'car_brand_id',	'modelo_id': 'model_id',	'combustible_id': 'fuel_id',	'cambio_id': 'gearbox_id'})

Ahora muestro de nuevo el DataFrame con los nombres cambiados

In [12]:
cars.columns

Index(['id_car', 'locate', 'car_brand', 'model', 'year', 'horses',
       'engine_power', 'km', 'fuel', 'gearbox', 'CO2', 'price', 'places',
       'deposit', '0_100km', 'displ_engine', 'marches', 'card_brand_id',
       'model_id', 'fuel_id', 'gearbox_id', 'localidad_id'],
      dtype='object')

### Preparación de los Datasets

In [13]:
# Lista de opcciones para transformar los dataframes
df_selector = ['complete', 'limit', 'less_limit', 'less_columns']
df_droppig = ['tensorflow', 'sklearn']

In [14]:
# Función para preparar los dataframes para no hacer código redundadnte
class Prepare():

  """
    La siguiente clase consta de 5 metodos, los cuales agilizan el tratamiento
    de los datos de un DataFrame.

    1. prepare_dataframes -> Permite realizar la limpieza sobre un dataframe
    dependiendo de lo que se quiera realizar
    2. dropping -> Permite quitar columnas del dataframe dependiendo de que
    libreria se vaya a utilizar
    3. reducer -> Permite reducir el tamaño de un DataFrame, en este caso
    cuando se selecciona less_columns
    4. limit -> Permite limitar los datos de un DataFrame
    5. limit_less -> Permite filtrar un DataFrame, en este caso filtra según
    el tamaño de coches en una marca.

    Esta clase la he creado para agilizar el tratamiento de los datos, en este
    caso, del DataFrame 'cars'.

  """

  def __init__(self):
    pass

  # Preparador de DataFrames
  def prepare_dataframes(self, df_selector, input_dataframe, df_droppig):

    # Sección de tipo de dataframe a preparar
    if df_selector == 'complete':
      print(f'Mostrando total filas y columnas:\n{input_dataframe.shape}', '\n')
      # Función que quita columnas
      dropping_data = self.dropping(input_dataframe, df_droppig)

      return dropping_data

    elif df_selector == 'limit':
      # Filtra las lineas del datraframe
      input_dataframe = self.limit(input_dataframe)
      print(f'Mostrando total filas y columnas:\n{input_dataframe.shape}', '\n')
      # Elimina las columnas del datraframe
      dropping = self.dropping(input_dataframe, df_droppig)
      return dropping
    
    elif df_selector == 'less_limit':
      # Filtra las lineas del datraframe
      input_dataframe = self.limit(input_dataframe)
      # Filtra las marcas con cantidad de coches inferior a 10
      input_dataframe = self.limit_less(input_dataframe)
      # Elimino las columnas
      dropping_data = self.dropping(input_dataframe, df_droppig)

      return dropping_data

    elif df_selector == 'less_columns':
      # Filtra las lineas del datraframe
      input_dataframe = self.limit(input_dataframe)
      # Filtra las marcas con cantidad de coches inferior a 10
      input_dataframe = self.limit_less(input_dataframe)
      # Elimino las columnas
      dropping_data = self.dropping(input_dataframe, df_droppig)
      # Elimino columnas extras
      input_dataframe = self.reducer(dropping_data, df_droppig)
      print(f'Mostrando reducción del total filas y columnas:\n{input_dataframe.shape}\n')
      
      return input_dataframe
      
  # Metodos para elimnar columnas
  def dropping(self, input_dataframe, df_droppig):

    if df_droppig == 'tensorflow':
      dropping = input_dataframe.drop(['id_car', 'card_brand_id', 'model_id', 
                                      'fuel_id', 'gearbox_id', 
                                      'localidad_id'], axis = 1)
      print(f'Listado de columnas despues del dropping: {dropping.columns}')
      return dropping

    elif df_droppig == 'sklearn':
      dropping = input_dataframe.drop(['id_car', 'locate', 'car_brand', 'model',
                                        'fuel', 'gearbox'], axis = 1)
      print(f'Listado de columnas despues del dropping: {dropping.columns}')
      return dropping

  # Metodo para eliminar columnas extras.
  def reducer(self, input_dataframe, df_droppig):

      if df_droppig == 'tensorflow':
        print('Reduciendo columnas...', '\n')
        dropping = input_dataframe.drop(['locate', 'engine_power',
                                         'CO2', 'places', 'deposit',
                                         '0_100km'], axis = 1)
        print('Columnas reducidas', '\n')
        print(f'Listado de columnas despues del dropping: {dropping.columns}', '\n')

        return dropping

      elif df_droppig == 'sklearn':
        print('Reduciendo columnas...', '\n')
        dropping = input_dataframe.drop(['engine_power','CO2', 'places',
                                         'deposit','0_100km', 'localidad_id'], axis = 1)
        print('Columnas reducidas', '\n')
        print(f'Listado de columnas despues del dropping: {dropping.columns}', '\n')

        return dropping
  
  # Metodos para quitar filas
  def limit(self, input_dataframe):

    input_dataframe = input_dataframe[(input_dataframe['price'] <= 80000) & (input_dataframe['km'] < 500000)]
    print(f"Mostrando el precio y los kilometros maximos:\n{input_dataframe[['price', 'km']].max()}", '\n')

    return input_dataframe

  # Metodo para seleccionar las marcas con cantidad de coches inferior a 10
  def limit_less(self, input_dataframe):

    # Cantidad de mracas con menos de 10 coches
      marks = input_dataframe['car_brand'].value_counts()

      # Guardo las marcas que tienen menos de coches
      cars_ten = marks[marks.values < 10]
      print(f'Coches de marcas con catidad < que 10: {sum(cars_ten.values)}', '\n')

      # Aplico la mascara anterior al dataframe con ~ delante indico que los valores True son False y viceversa para el isin()
      input_dataframe = input_dataframe[~input_dataframe['car_brand'].isin(cars_ten.index)]
      print(f'Mostrando total filas y columnas:\n{input_dataframe.shape}', '\n')

      return input_dataframe


In [15]:
# Instancio la clase Prepare
P = Prepare()

Ahora lo que voy a realizar es la creación de un diccionario el cual va a albergar 8 dataframes, 4 para TensorFlow y otros 4 para Sklearn, tratados previamente por la clase del bloque anterior.

In [16]:
# Diccionario para almacenar los DataFrames según libreria a usar.
dict_dataframes = {'tensorflow': {}, 'sklearn': {}}

In [17]:
# bucles para ejecutar la clase y almacenar los resultados en el diccionario del bloque anterior.
for i in range(len(df_selector)):
  for x in range(len(df_droppig)):

    if x == 0:
      print(df_selector[i], df_droppig[x], '\n')
      cars_tf = P.prepare_dataframes(df_selector[i], cars, df_droppig[x])
    elif x == 1:
      print(df_selector[i], df_droppig[x], '\n')
      cars_sk = P.prepare_dataframes(df_selector[i], cars, df_droppig[x])
  
  dict_dataframes['tensorflow'][df_selector[i]] = cars_tf
  dict_dataframes['sklearn'][df_selector[i]] = cars_sk

complete tensorflow 

Mostrando total filas y columnas:
(179502, 22) 

Listado de columnas despues del dropping: Index(['locate', 'car_brand', 'model', 'year', 'horses', 'engine_power', 'km',
       'fuel', 'gearbox', 'CO2', 'price', 'places', 'deposit', '0_100km',
       'displ_engine', 'marches'],
      dtype='object')
complete sklearn 

Mostrando total filas y columnas:
(179502, 22) 

Listado de columnas despues del dropping: Index(['year', 'horses', 'engine_power', 'km', 'CO2', 'price', 'places',
       'deposit', '0_100km', 'displ_engine', 'marches', 'card_brand_id',
       'model_id', 'fuel_id', 'gearbox_id', 'localidad_id'],
      dtype='object')
limit tensorflow 

Mostrando el precio y los kilometros maximos:
price     80000.0
km       496000.0
dtype: float64 

Mostrando total filas y columnas:
(176552, 22) 

Listado de columnas despues del dropping: Index(['locate', 'car_brand', 'model', 'year', 'horses', 'engine_power', 'km',
       'fuel', 'gearbox', 'CO2', 'price', 'places'

##### DataFrames para los algoritmos de TensorFlow

In [18]:
dict_dataframes['tensorflow']['complete']

locate      car_brand                    model    year  horses  \
0           Madrid        Citroen      Citroen C3 aircross  2022.0   110.0   
1       Pontevedra        Renault           Renault Scénic  2017.0   130.0   
2        Barcelona           Ford     Ford Tourneo courier  2019.0    95.0   
3           Madrid        Renault           Renault Scénic  2019.0   110.0   
4       Pontevedra         Nissan            Nissan Pulsar  2016.0   110.0   
...            ...            ...                      ...     ...     ...   
179497   Barcelona  Mercedes-benz  Mercedes-benz Clase slk  2013.0   184.0   
179498     Vizcaya  Mercedes-benz    Mercedes-benz Clase e  2018.0   245.0   
179499     Vizcaya        Peugeot             Peugeot 3008  2015.0   121.0   
179500    Valencia  Mercedes-benz  Mercedes-benz Clase gla  2018.0   136.0   
179501   Barcelona  Mercedes-benz    Mercedes-benz Clase c  2013.0   136.0   

        engine_power        km      fuel     gearbox    CO2    price  places  \
0               81.0    7119.0  Gasolina      Manual    0.0  19900.0     5.0   
1               96.0   43618.0  Gasolina      Manual  129.0  18975.0     5.0   
2               71.0  153880.0    Diesel      Manual  104.0  10900.0     5.0   
3               81.0   73238.0    Diesel      Manual  105.0  19500.0     5.0   
4               81.0   82765.0    Diesel      Manual   94.0  13500.0     5.0   
...              ...       ...       ...         ...    ...      ...     ...   
179497         135.0   37379.0  Gasolina      Manual  142.0  24986.0     2.0   
179498         180.0   69780.0  Gasolina  Automático  167.0  39999.0     4.0   
179499          88.0   97945.0    Diesel      Manual  108.0  13750.0     5.0   
179500         100.0   53193.0    Diesel  Automático  108.0  29990.0     5.0   
179501         100.0  139695.0    Diesel      Manual  127.0  15180.0     5.0   

        deposit  0_100km  displ_engine  marches  
0          45.0      8.8        1199.0      6.0  
1          52.0     12.3        1198.0      6.0  
2          47.0      0.0        1498.0      5.0  
3          60.0     12.5        1461.0      6.0  
4          46.0     11.5        1461.0      6.0  
...         ...      ...           ...      ...  
179497     60.0      7.3        1796.0      6.0  
179498     66.0      6.6        1991.0      9.0  
179499     60.0     12.0        1560.0      6.0  
179500     50.0      9.1        2143.0      7.0  
179501     59.0      9.2        2143.0      6.0  

[179502 rows x 16 columns]

In [19]:
tf_complete = dict_dataframes['tensorflow']['complete'].corr()
correlations(tf_complete)

In [20]:
dict_dataframes['tensorflow']['limit']

locate      car_brand                    model    year  horses  \
0           Madrid        Citroen      Citroen C3 aircross  2022.0   110.0   
1       Pontevedra        Renault           Renault Scénic  2017.0   130.0   
2        Barcelona           Ford     Ford Tourneo courier  2019.0    95.0   
3           Madrid        Renault           Renault Scénic  2019.0   110.0   
4       Pontevedra         Nissan            Nissan Pulsar  2016.0   110.0   
...            ...            ...                      ...     ...     ...   
179497   Barcelona  Mercedes-benz  Mercedes-benz Clase slk  2013.0   184.0   
179498     Vizcaya  Mercedes-benz    Mercedes-benz Clase e  2018.0   245.0   
179499     Vizcaya        Peugeot             Peugeot 3008  2015.0   121.0   
179500    Valencia  Mercedes-benz  Mercedes-benz Clase gla  2018.0   136.0   
179501   Barcelona  Mercedes-benz    Mercedes-benz Clase c  2013.0   136.0   

        engine_power        km      fuel     gearbox    CO2    price  places  \
0               81.0    7119.0  Gasolina      Manual    0.0  19900.0     5.0   
1               96.0   43618.0  Gasolina      Manual  129.0  18975.0     5.0   
2               71.0  153880.0    Diesel      Manual  104.0  10900.0     5.0   
3               81.0   73238.0    Diesel      Manual  105.0  19500.0     5.0   
4               81.0   82765.0    Diesel      Manual   94.0  13500.0     5.0   
...              ...       ...       ...         ...    ...      ...     ...   
179497         135.0   37379.0  Gasolina      Manual  142.0  24986.0     2.0   
179498         180.0   69780.0  Gasolina  Automático  167.0  39999.0     4.0   
179499          88.0   97945.0    Diesel      Manual  108.0  13750.0     5.0   
179500         100.0   53193.0    Diesel  Automático  108.0  29990.0     5.0   
179501         100.0  139695.0    Diesel      Manual  127.0  15180.0     5.0   

        deposit  0_100km  displ_engine  marches  
0          45.0      8.8        1199.0      6.0  
1          52.0     12.3        1198.0      6.0  
2          47.0      0.0        1498.0      5.0  
3          60.0     12.5        1461.0      6.0  
4          46.0     11.5        1461.0      6.0  
...         ...      ...           ...      ...  
179497     60.0      7.3        1796.0      6.0  
179498     66.0      6.6        1991.0      9.0  
179499     60.0     12.0        1560.0      6.0  
179500     50.0      9.1        2143.0      7.0  
179501     59.0      9.2        2143.0      6.0  

[176552 rows x 16 columns]

In [21]:
tf_limit = dict_dataframes['tensorflow']['limit'].corr()
correlations(tf_limit)

In [22]:
dict_dataframes['tensorflow']['less_limit']

locate      car_brand                    model    year  horses  \
0           Madrid        Citroen      Citroen C3 aircross  2022.0   110.0   
1       Pontevedra        Renault           Renault Scénic  2017.0   130.0   
2        Barcelona           Ford     Ford Tourneo courier  2019.0    95.0   
3           Madrid        Renault           Renault Scénic  2019.0   110.0   
4       Pontevedra         Nissan            Nissan Pulsar  2016.0   110.0   
...            ...            ...                      ...     ...     ...   
179497   Barcelona  Mercedes-benz  Mercedes-benz Clase slk  2013.0   184.0   
179498     Vizcaya  Mercedes-benz    Mercedes-benz Clase e  2018.0   245.0   
179499     Vizcaya        Peugeot             Peugeot 3008  2015.0   121.0   
179500    Valencia  Mercedes-benz  Mercedes-benz Clase gla  2018.0   136.0   
179501   Barcelona  Mercedes-benz    Mercedes-benz Clase c  2013.0   136.0   

        engine_power        km      fuel     gearbox    CO2    price  places  \
0               81.0    7119.0  Gasolina      Manual    0.0  19900.0     5.0   
1               96.0   43618.0  Gasolina      Manual  129.0  18975.0     5.0   
2               71.0  153880.0    Diesel      Manual  104.0  10900.0     5.0   
3               81.0   73238.0    Diesel      Manual  105.0  19500.0     5.0   
4               81.0   82765.0    Diesel      Manual   94.0  13500.0     5.0   
...              ...       ...       ...         ...    ...      ...     ...   
179497         135.0   37379.0  Gasolina      Manual  142.0  24986.0     2.0   
179498         180.0   69780.0  Gasolina  Automático  167.0  39999.0     4.0   
179499          88.0   97945.0    Diesel      Manual  108.0  13750.0     5.0   
179500         100.0   53193.0    Diesel  Automático  108.0  29990.0     5.0   
179501         100.0  139695.0    Diesel      Manual  127.0  15180.0     5.0   

        deposit  0_100km  displ_engine  marches  
0          45.0      8.8        1199.0      6.0  
1          52.0     12.3        1198.0      6.0  
2          47.0      0.0        1498.0      5.0  
3          60.0     12.5        1461.0      6.0  
4          46.0     11.5        1461.0      6.0  
...         ...      ...           ...      ...  
179497     60.0      7.3        1796.0      6.0  
179498     66.0      6.6        1991.0      9.0  
179499     60.0     12.0        1560.0      6.0  
179500     50.0      9.1        2143.0      7.0  
179501     59.0      9.2        2143.0      6.0  

[176492 rows x 16 columns]

In [23]:
tf_less_limit = dict_dataframes['tensorflow']['less_limit'].corr()
correlations(tf_less_limit)

In [24]:
dict_dataframes['tensorflow']['less_columns']

car_brand                    model    year  horses        km  \
0             Citroen      Citroen C3 aircross  2022.0   110.0    7119.0   
1             Renault           Renault Scénic  2017.0   130.0   43618.0   
2                Ford     Ford Tourneo courier  2019.0    95.0  153880.0   
3             Renault           Renault Scénic  2019.0   110.0   73238.0   
4              Nissan            Nissan Pulsar  2016.0   110.0   82765.0   
...               ...                      ...     ...     ...       ...   
179497  Mercedes-benz  Mercedes-benz Clase slk  2013.0   184.0   37379.0   
179498  Mercedes-benz    Mercedes-benz Clase e  2018.0   245.0   69780.0   
179499        Peugeot             Peugeot 3008  2015.0   121.0   97945.0   
179500  Mercedes-benz  Mercedes-benz Clase gla  2018.0   136.0   53193.0   
179501  Mercedes-benz    Mercedes-benz Clase c  2013.0   136.0  139695.0   

            fuel     gearbox    price  displ_engine  marches  
0       Gasolina      Manual  19900.0        1199.0      6.0  
1       Gasolina      Manual  18975.0        1198.0      6.0  
2         Diesel      Manual  10900.0        1498.0      5.0  
3         Diesel      Manual  19500.0        1461.0      6.0  
4         Diesel      Manual  13500.0        1461.0      6.0  
...          ...         ...      ...           ...      ...  
179497  Gasolina      Manual  24986.0        1796.0      6.0  
179498  Gasolina  Automático  39999.0        1991.0      9.0  
179499    Diesel      Manual  13750.0        1560.0      6.0  
179500    Diesel  Automático  29990.0        2143.0      7.0  
179501    Diesel      Manual  15180.0        2143.0      6.0  

[176492 rows x 10 columns]

In [25]:
tf_less_columns = dict_dataframes['tensorflow']['less_columns'].corr()
correlations(tf_less_columns)

##### DataFrames para el algoritmo de Sklearn

In [26]:
dict_dataframes['sklearn']['complete']

year  horses  engine_power        km    CO2    price  places  \
0       2022.0   110.0          81.0    7119.0    0.0  19900.0     5.0   
1       2017.0   130.0          96.0   43618.0  129.0  18975.0     5.0   
2       2019.0    95.0          71.0  153880.0  104.0  10900.0     5.0   
3       2019.0   110.0          81.0   73238.0  105.0  19500.0     5.0   
4       2016.0   110.0          81.0   82765.0   94.0  13500.0     5.0   
...        ...     ...           ...       ...    ...      ...     ...   
179497  2013.0   184.0         135.0   37379.0  142.0  24986.0     2.0   
179498  2018.0   245.0         180.0   69780.0  167.0  39999.0     4.0   
179499  2015.0   121.0          88.0   97945.0  108.0  13750.0     5.0   
179500  2018.0   136.0         100.0   53193.0  108.0  29990.0     5.0   
179501  2013.0   136.0         100.0  139695.0  127.0  15180.0     5.0   

        deposit  0_100km  displ_engine  marches  card_brand_id  model_id  \
0          45.0      8.8        1199.0      6.0           10.0     118.0   
1          52.0     12.3        1198.0      6.0           54.0     558.0   
2          47.0      0.0        1498.0      5.0           20.0     239.0   
3          60.0     12.5        1461.0      6.0           54.0     558.0   
4          46.0     11.5        1461.0      6.0           49.0     475.0   
...         ...      ...           ...      ...            ...       ...   
179497     60.0      7.3        1796.0      6.0           44.0     429.0   
179498     66.0      6.6        1991.0      9.0           44.0     415.0   
179499     60.0     12.0        1560.0      6.0           51.0     512.0   
179500     50.0      9.1        2143.0      7.0           44.0     418.0   
179501     59.0      9.2        2143.0      6.0           44.0     409.0   

        fuel_id  gearbox_id  localidad_id  
0           3.0         1.0          28.0  
1           3.0         1.0          34.0  
2           1.0         1.0           5.0  
3           1.0         1.0          28.0  
4           1.0         1.0          34.0  
...         ...         ...           ...  
179497      3.0         1.0           5.0  
179498      3.0         0.0          45.0  
179499      1.0         1.0          45.0  
179500      1.0         0.0          43.0  
179501      1.0         1.0           5.0  

[179502 rows x 16 columns]

In [27]:
sk_coplete = dict_dataframes['sklearn']['complete'].corr()
correlations(sk_coplete)

In [28]:
dict_dataframes['sklearn']['limit']

year  horses  engine_power        km    CO2    price  places  \
0       2022.0   110.0          81.0    7119.0    0.0  19900.0     5.0   
1       2017.0   130.0          96.0   43618.0  129.0  18975.0     5.0   
2       2019.0    95.0          71.0  153880.0  104.0  10900.0     5.0   
3       2019.0   110.0          81.0   73238.0  105.0  19500.0     5.0   
4       2016.0   110.0          81.0   82765.0   94.0  13500.0     5.0   
...        ...     ...           ...       ...    ...      ...     ...   
179497  2013.0   184.0         135.0   37379.0  142.0  24986.0     2.0   
179498  2018.0   245.0         180.0   69780.0  167.0  39999.0     4.0   
179499  2015.0   121.0          88.0   97945.0  108.0  13750.0     5.0   
179500  2018.0   136.0         100.0   53193.0  108.0  29990.0     5.0   
179501  2013.0   136.0         100.0  139695.0  127.0  15180.0     5.0   

        deposit  0_100km  displ_engine  marches  card_brand_id  model_id  \
0          45.0      8.8        1199.0      6.0           10.0     118.0   
1          52.0     12.3        1198.0      6.0           54.0     558.0   
2          47.0      0.0        1498.0      5.0           20.0     239.0   
3          60.0     12.5        1461.0      6.0           54.0     558.0   
4          46.0     11.5        1461.0      6.0           49.0     475.0   
...         ...      ...           ...      ...            ...       ...   
179497     60.0      7.3        1796.0      6.0           44.0     429.0   
179498     66.0      6.6        1991.0      9.0           44.0     415.0   
179499     60.0     12.0        1560.0      6.0           51.0     512.0   
179500     50.0      9.1        2143.0      7.0           44.0     418.0   
179501     59.0      9.2        2143.0      6.0           44.0     409.0   

        fuel_id  gearbox_id  localidad_id  
0           3.0         1.0          28.0  
1           3.0         1.0          34.0  
2           1.0         1.0           5.0  
3           1.0         1.0          28.0  
4           1.0         1.0          34.0  
...         ...         ...           ...  
179497      3.0         1.0           5.0  
179498      3.0         0.0          45.0  
179499      1.0         1.0          45.0  
179500      1.0         0.0          43.0  
179501      1.0         1.0           5.0  

[176552 rows x 16 columns]

In [29]:
sk_limit = dict_dataframes['sklearn']['limit'].corr()
correlations(sk_limit)

In [30]:
dict_dataframes['sklearn']['less_limit']

year  horses  engine_power        km    CO2    price  places  \
0       2022.0   110.0          81.0    7119.0    0.0  19900.0     5.0   
1       2017.0   130.0          96.0   43618.0  129.0  18975.0     5.0   
2       2019.0    95.0          71.0  153880.0  104.0  10900.0     5.0   
3       2019.0   110.0          81.0   73238.0  105.0  19500.0     5.0   
4       2016.0   110.0          81.0   82765.0   94.0  13500.0     5.0   
...        ...     ...           ...       ...    ...      ...     ...   
179497  2013.0   184.0         135.0   37379.0  142.0  24986.0     2.0   
179498  2018.0   245.0         180.0   69780.0  167.0  39999.0     4.0   
179499  2015.0   121.0          88.0   97945.0  108.0  13750.0     5.0   
179500  2018.0   136.0         100.0   53193.0  108.0  29990.0     5.0   
179501  2013.0   136.0         100.0  139695.0  127.0  15180.0     5.0   

        deposit  0_100km  displ_engine  marches  card_brand_id  model_id  \
0          45.0      8.8        1199.0      6.0           10.0     118.0   
1          52.0     12.3        1198.0      6.0           54.0     558.0   
2          47.0      0.0        1498.0      5.0           20.0     239.0   
3          60.0     12.5        1461.0      6.0           54.0     558.0   
4          46.0     11.5        1461.0      6.0           49.0     475.0   
...         ...      ...           ...      ...            ...       ...   
179497     60.0      7.3        1796.0      6.0           44.0     429.0   
179498     66.0      6.6        1991.0      9.0           44.0     415.0   
179499     60.0     12.0        1560.0      6.0           51.0     512.0   
179500     50.0      9.1        2143.0      7.0           44.0     418.0   
179501     59.0      9.2        2143.0      6.0           44.0     409.0   

        fuel_id  gearbox_id  localidad_id  
0           3.0         1.0          28.0  
1           3.0         1.0          34.0  
2           1.0         1.0           5.0  
3           1.0         1.0          28.0  
4           1.0         1.0          34.0  
...         ...         ...           ...  
179497      3.0         1.0           5.0  
179498      3.0         0.0          45.0  
179499      1.0         1.0          45.0  
179500      1.0         0.0          43.0  
179501      1.0         1.0           5.0  

[176492 rows x 16 columns]

In [31]:
sk_less_limit = dict_dataframes['sklearn']['less_limit'].corr()
correlations(sk_less_limit)

In [32]:
dict_dataframes['sklearn']['less_columns']

year  horses        km    price  displ_engine  marches  \
0       2022.0   110.0    7119.0  19900.0        1199.0      6.0   
1       2017.0   130.0   43618.0  18975.0        1198.0      6.0   
2       2019.0    95.0  153880.0  10900.0        1498.0      5.0   
3       2019.0   110.0   73238.0  19500.0        1461.0      6.0   
4       2016.0   110.0   82765.0  13500.0        1461.0      6.0   
...        ...     ...       ...      ...           ...      ...   
179497  2013.0   184.0   37379.0  24986.0        1796.0      6.0   
179498  2018.0   245.0   69780.0  39999.0        1991.0      9.0   
179499  2015.0   121.0   97945.0  13750.0        1560.0      6.0   
179500  2018.0   136.0   53193.0  29990.0        2143.0      7.0   
179501  2013.0   136.0  139695.0  15180.0        2143.0      6.0   

        card_brand_id  model_id  fuel_id  gearbox_id  
0                10.0     118.0      3.0         1.0  
1                54.0     558.0      3.0         1.0  
2                20.0     239.0      1.0         1.0  
3                54.0     558.0      1.0         1.0  
4                49.0     475.0      1.0         1.0  
...               ...       ...      ...         ...  
179497           44.0     429.0      3.0         1.0  
179498           44.0     415.0      3.0         0.0  
179499           51.0     512.0      1.0         1.0  
179500           44.0     418.0      1.0         0.0  
179501           44.0     409.0      1.0         1.0  

[176492 rows x 10 columns]

In [33]:
sk_less_columns = dict_dataframes['sklearn']['less_columns'].corr()
correlations(sk_less_columns)

### Comprobaciones

#### Dataset completo.

Para TensorFlow

In [34]:
cars_tf = P.prepare_dataframes(df_selector[0], cars, df_droppig[0])

Mostrando total filas y columnas:
(179502, 22) 

Listado de columnas despues del dropping: Index(['locate', 'car_brand', 'model', 'year', 'horses', 'engine_power', 'km',
       'fuel', 'gearbox', 'CO2', 'price', 'places', 'deposit', '0_100km',
       'displ_engine', 'marches'],
      dtype='object')


In [35]:
cars_tf.head(1)

locate car_brand                model    year  horses  engine_power  \
0  Madrid   Citroen  Citroen C3 aircross  2022.0   110.0          81.0   

       km      fuel gearbox  CO2    price  places  deposit  0_100km  \
0  7119.0  Gasolina  Manual  0.0  19900.0     5.0     45.0      8.8   

   displ_engine  marches  
0        1199.0      6.0

Para Sklearn

In [36]:
cars_sk = P.prepare_dataframes(df_selector[0], cars, df_droppig[1])

Mostrando total filas y columnas:
(179502, 22) 

Listado de columnas despues del dropping: Index(['year', 'horses', 'engine_power', 'km', 'CO2', 'price', 'places',
       'deposit', '0_100km', 'displ_engine', 'marches', 'card_brand_id',
       'model_id', 'fuel_id', 'gearbox_id', 'localidad_id'],
      dtype='object')


In [37]:
cars_sk.head(1)

year  horses  engine_power      km  CO2    price  places  deposit  \
0  2022.0   110.0          81.0  7119.0  0.0  19900.0     5.0     45.0   

   0_100km  displ_engine  marches  card_brand_id  model_id  fuel_id  \
0      8.8        1199.0      6.0           10.0     118.0      3.0   

   gearbox_id  localidad_id  
0         1.0          28.0

#### Dataset limitando el precio y los kilometros

Ahora lo que realizo es el filtro de datos según las visualizaciones anteriormente vistas, donde determine que lo mejor era quitar los coches con mas de 500.000 kilometros y con un precio superior a 80.000€

Este nuevo DataFrame lo guardare con el nombre de cars_limit

Para TensorFlow

In [38]:
cars_limit_tf = P.prepare_dataframes(df_selector[1], cars, df_droppig[0])

Mostrando el precio y los kilometros maximos:
price     80000.0
km       496000.0
dtype: float64 

Mostrando total filas y columnas:
(176552, 22) 

Listado de columnas despues del dropping: Index(['locate', 'car_brand', 'model', 'year', 'horses', 'engine_power', 'km',
       'fuel', 'gearbox', 'CO2', 'price', 'places', 'deposit', '0_100km',
       'displ_engine', 'marches'],
      dtype='object')


In [39]:
cars_limit_tf.head(1)

locate car_brand                model    year  horses  engine_power  \
0  Madrid   Citroen  Citroen C3 aircross  2022.0   110.0          81.0   

       km      fuel gearbox  CO2    price  places  deposit  0_100km  \
0  7119.0  Gasolina  Manual  0.0  19900.0     5.0     45.0      8.8   

   displ_engine  marches  
0        1199.0      6.0

Para Sklearn

In [40]:
cars_limit_sk = P.prepare_dataframes(df_selector[1], cars, df_droppig[1])

Mostrando el precio y los kilometros maximos:
price     80000.0
km       496000.0
dtype: float64 

Mostrando total filas y columnas:
(176552, 22) 

Listado de columnas despues del dropping: Index(['year', 'horses', 'engine_power', 'km', 'CO2', 'price', 'places',
       'deposit', '0_100km', 'displ_engine', 'marches', 'card_brand_id',
       'model_id', 'fuel_id', 'gearbox_id', 'localidad_id'],
      dtype='object')


In [41]:
cars_limit_sk.head(1)

year  horses  engine_power      km  CO2    price  places  deposit  \
0  2022.0   110.0          81.0  7119.0  0.0  19900.0     5.0     45.0   

   0_100km  displ_engine  marches  card_brand_id  model_id  fuel_id  \
0      8.8        1199.0      6.0           10.0     118.0      3.0   

   gearbox_id  localidad_id  
0         1.0          28.0

#### Dataset limitando el precio, los kilometros y las marcas con coches con cantidad inferior a 10 

Para TensorFlow

In [42]:
cars_tf_less_ten = P.prepare_dataframes(df_selector[2], cars, df_droppig[0])

Mostrando el precio y los kilometros maximos:
price     80000.0
km       496000.0
dtype: float64 

Coches de marcas con catidad < que 10: 60 

Mostrando total filas y columnas:
(176492, 22) 

Listado de columnas despues del dropping: Index(['locate', 'car_brand', 'model', 'year', 'horses', 'engine_power', 'km',
       'fuel', 'gearbox', 'CO2', 'price', 'places', 'deposit', '0_100km',
       'displ_engine', 'marches'],
      dtype='object')


In [43]:
cars_tf_less_ten.head(1)

locate car_brand                model    year  horses  engine_power  \
0  Madrid   Citroen  Citroen C3 aircross  2022.0   110.0          81.0   

       km      fuel gearbox  CO2    price  places  deposit  0_100km  \
0  7119.0  Gasolina  Manual  0.0  19900.0     5.0     45.0      8.8   

   displ_engine  marches  
0        1199.0      6.0

Para Sklearn

In [44]:
cars_sk_less_ten = P.prepare_dataframes(df_selector[2], cars, df_droppig[1])

Mostrando el precio y los kilometros maximos:
price     80000.0
km       496000.0
dtype: float64 

Coches de marcas con catidad < que 10: 60 

Mostrando total filas y columnas:
(176492, 22) 

Listado de columnas despues del dropping: Index(['year', 'horses', 'engine_power', 'km', 'CO2', 'price', 'places',
       'deposit', '0_100km', 'displ_engine', 'marches', 'card_brand_id',
       'model_id', 'fuel_id', 'gearbox_id', 'localidad_id'],
      dtype='object')


In [45]:
cars_sk_less_ten.head(1)

year  horses  engine_power      km  CO2    price  places  deposit  \
0  2022.0   110.0          81.0  7119.0  0.0  19900.0     5.0     45.0   

   0_100km  displ_engine  marches  card_brand_id  model_id  fuel_id  \
0      8.8        1199.0      6.0           10.0     118.0      3.0   

   gearbox_id  localidad_id  
0         1.0          28.0

In [46]:
cars_sk_less_ten.shape

(176492, 16)

#### Dataset limitando el precio, los kilometros, las marcas con coches con cantidad inferior a 10 y dejando solo mas columas de `car_brand`, `model`, `year`, `horses`, `km`, `fuel`, `gearbox`, `price`, `displacement_engine`, `marches`

Para Tensorflow

In [47]:
cars_tf_drop = P.prepare_dataframes(df_selector[3], cars, df_droppig[0])

Mostrando el precio y los kilometros maximos:
price     80000.0
km       496000.0
dtype: float64 

Coches de marcas con catidad < que 10: 60 

Mostrando total filas y columnas:
(176492, 22) 

Listado de columnas despues del dropping: Index(['locate', 'car_brand', 'model', 'year', 'horses', 'engine_power', 'km',
       'fuel', 'gearbox', 'CO2', 'price', 'places', 'deposit', '0_100km',
       'displ_engine', 'marches'],
      dtype='object')
Reduciendo columnas... 

Columnas reducidas 

Listado de columnas despues del dropping: Index(['car_brand', 'model', 'year', 'horses', 'km', 'fuel', 'gearbox',
       'price', 'displ_engine', 'marches'],
      dtype='object') 

Mostrando reducción del total filas y columnas:
(176492, 10)



In [48]:
cars_tf_drop

car_brand                    model    year  horses        km  \
0             Citroen      Citroen C3 aircross  2022.0   110.0    7119.0   
1             Renault           Renault Scénic  2017.0   130.0   43618.0   
2                Ford     Ford Tourneo courier  2019.0    95.0  153880.0   
3             Renault           Renault Scénic  2019.0   110.0   73238.0   
4              Nissan            Nissan Pulsar  2016.0   110.0   82765.0   
...               ...                      ...     ...     ...       ...   
179497  Mercedes-benz  Mercedes-benz Clase slk  2013.0   184.0   37379.0   
179498  Mercedes-benz    Mercedes-benz Clase e  2018.0   245.0   69780.0   
179499        Peugeot             Peugeot 3008  2015.0   121.0   97945.0   
179500  Mercedes-benz  Mercedes-benz Clase gla  2018.0   136.0   53193.0   
179501  Mercedes-benz    Mercedes-benz Clase c  2013.0   136.0  139695.0   

            fuel     gearbox    price  displ_engine  marches  
0       Gasolina      Manual  19900.0        1199.0      6.0  
1       Gasolina      Manual  18975.0        1198.0      6.0  
2         Diesel      Manual  10900.0        1498.0      5.0  
3         Diesel      Manual  19500.0        1461.0      6.0  
4         Diesel      Manual  13500.0        1461.0      6.0  
...          ...         ...      ...           ...      ...  
179497  Gasolina      Manual  24986.0        1796.0      6.0  
179498  Gasolina  Automático  39999.0        1991.0      9.0  
179499    Diesel      Manual  13750.0        1560.0      6.0  
179500    Diesel  Automático  29990.0        2143.0      7.0  
179501    Diesel      Manual  15180.0        2143.0      6.0  

[176492 rows x 10 columns]

Para Sklearn

In [49]:
cars_sk_drop = P.prepare_dataframes(df_selector[3], cars, df_droppig[1])

Mostrando el precio y los kilometros maximos:
price     80000.0
km       496000.0
dtype: float64 

Coches de marcas con catidad < que 10: 60 

Mostrando total filas y columnas:
(176492, 22) 

Listado de columnas despues del dropping: Index(['year', 'horses', 'engine_power', 'km', 'CO2', 'price', 'places',
       'deposit', '0_100km', 'displ_engine', 'marches', 'card_brand_id',
       'model_id', 'fuel_id', 'gearbox_id', 'localidad_id'],
      dtype='object')
Reduciendo columnas... 

Columnas reducidas 

Listado de columnas despues del dropping: Index(['year', 'horses', 'km', 'price', 'displ_engine', 'marches',
       'card_brand_id', 'model_id', 'fuel_id', 'gearbox_id'],
      dtype='object') 

Mostrando reducción del total filas y columnas:
(176492, 10)



In [50]:
cars_sk_drop

year  horses        km    price  displ_engine  marches  \
0       2022.0   110.0    7119.0  19900.0        1199.0      6.0   
1       2017.0   130.0   43618.0  18975.0        1198.0      6.0   
2       2019.0    95.0  153880.0  10900.0        1498.0      5.0   
3       2019.0   110.0   73238.0  19500.0        1461.0      6.0   
4       2016.0   110.0   82765.0  13500.0        1461.0      6.0   
...        ...     ...       ...      ...           ...      ...   
179497  2013.0   184.0   37379.0  24986.0        1796.0      6.0   
179498  2018.0   245.0   69780.0  39999.0        1991.0      9.0   
179499  2015.0   121.0   97945.0  13750.0        1560.0      6.0   
179500  2018.0   136.0   53193.0  29990.0        2143.0      7.0   
179501  2013.0   136.0  139695.0  15180.0        2143.0      6.0   

        card_brand_id  model_id  fuel_id  gearbox_id  
0                10.0     118.0      3.0         1.0  
1                54.0     558.0      3.0         1.0  
2                20.0     239.0      1.0         1.0  
3                54.0     558.0      1.0         1.0  
4                49.0     475.0      1.0         1.0  
...               ...       ...      ...         ...  
179497           44.0     429.0      3.0         1.0  
179498           44.0     415.0      3.0         0.0  
179499           51.0     512.0      1.0         1.0  
179500           44.0     418.0      1.0         0.0  
179501           44.0     409.0      1.0         1.0  

[176492 rows x 10 columns]

### Machine Lerning - TensorFlow

En principio voy a probar 2 modelos:

1. Random Forest - `tfdf.keras.RandomForestModel`
2. Gradient Boosted Trees Model - `tfdf.keras.GradientBoostedTreesModel`

Por otro lado voy a probar con varios tratamientos de los datos:

1. Todos los datos del CSV
2. Filtrando por precio no seperior a 80.000€ y kilometros no superior a 500.000
3. Filtrando por cantidad de modelos en las marcas, superior a 10.
4. Retirando las columnas de `marca_id`	`modelo_id`	`combustible_id`	`cambio_id`
5. Retirando lo anterior mas alguna columna mas que no tenga mucha correlación con el precio, por ejemplo eliminando `engine_power`
6. Retirando las columnas `engine_power`, `deposit`, `CO2`, `places`, `0_100km` del punto anterior

In [51]:
class Mlearn():

  def __init__(self):
    pass

  # Metodo para entrenar un Gradient Boosted
  def tensorflow_bg(self, input_dataframe, train):

      # Especificar las opciones del modelo
      model_car = tfdf.keras.GradientBoostedTreesModel(
      task=tfdf.keras.Task.REGRESSION,
      validation_ratio = 0.1,
      num_trees = 100,
      max_depth = 10,
      l1_regularization = 0.01,
      l2_regularization = 0.01,
      early_stopping = 'LOSS_INCREASE',
      loss = "SQUARED_ERROR")

      # Entrenar el modelo
      model_car.fit(train)

      return model_car

  def tensorflow_rf(self, input_dataframe, train):

      # Especificar las opciones del modelo
      model_car = tfdf.keras.RandomForestModel(
      task=tfdf.keras.Task.REGRESSION,
      num_trees = 100,
      max_depth = 10,
      split_axis = "AXIS_ALIGNED",
      categorical_algorithm = "CART")

      # Entrenar el modelo
      model_car.fit(train)

      return model_car

In [52]:
# Instancio la clase Mlearn
ML = Mlearn()

In [53]:
dict_tr_ts = {}

for index, df in enumerate(dict_dataframes['tensorflow']):

  data_frame = dict_dataframes['tensorflow'][df]

  # Separo los datos de entrenamiento (train) y los de test (test)
  train, test = train_test_split(data_frame, test_size=0.2, random_state=42)
        
  # Especificar la columna de la variable de destino (o target)
  target = "price"

  # Convertir el DataFrame de pandas a un conjunto de datos de TensorFlow
  train_cars = tfdf.keras.pd_dataframe_to_tf_dataset(train, label=target, task=tfdf.keras.Task.REGRESSION)
  test_cars = tfdf.keras.pd_dataframe_to_tf_dataset(test, label=target, task=tfdf.keras.Task.REGRESSION)

  # Añado el test_cars al diccionario para poder usarlo despues
  dict_tr_ts.update({df:[test, test_cars]})

  # Entreno el modelo GradientBoosted 
  model_car_bg = ML.tensorflow_bg(data_frame, train_cars)

  # Guardo el modelo GradientBoosted en Drive
  model_car_bg.save(f'/content/drive/MyDrive/Colab Notebooks/Curso_IA_BIGDATA/TFM/export_models/Gredient_Boosted_TensowFlow/model_bg_{df}')

  # Entreno el modelo RandomForest 
  model_car_rf = ML.tensorflow_rf(data_frame, train_cars)

  # Guardo el modelo RandomForest en Drive
  model_car_rf.save(f'/content/drive/MyDrive/Colab Notebooks/Curso_IA_BIGDATA/TFM/export_models/Random_forest_TensorFlow/model_rf_{df}')

Use /tmp/tmpko51ia70 as temporary training directory
Reading training dataset...


Instructions for updating:
Lambda fuctions will be no more assumed to be used in the statement where they are used, or at least in the same block. https://github.com/tensorflow/tensorflow/issues/56089


Training dataset read in 0:00:19.410553. Found 143601 examples.
Training model...
Model trained in 0:01:36.827518
Compiling model...


Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: could not get source code
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert


Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: could not get source code
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
Model compiled.


...

Use /tmp/tmpyyblaro9 as temporary training directory
Reading training dataset...


Training dataset read in 0:00:01.716243. Found 141193 examples.
Training model...
Model trained in 0:01:26.006117
Compiling model...


Model compiled.


Use /tmp/tmpo3bi8pgr as temporary training directory
Reading training dataset...
Training dataset read in 0:00:01.118254. Found 141193 examples.
Training model...
Model trained in 0:02:40.392096
Compiling model...
Model compiled.


Use /tmp/tmpaunp6hnh as temporary training directory
Reading training dataset...
Training dataset read in 0:00:03.705657. Found 141193 examples.
Training model...
Model trained in 0:01:17.095556
Compiling model...
Model compiled.


Modelos de GradientBoosted - TensorFlow


In [54]:
model_bg_complete = load_model('/content/drive/MyDrive/Colab Notebooks/Curso_IA_BIGDATA/TFM/export_models/Gredient_Boosted_TensowFlow/model_bg_complete', compile = False)
model_bg_limit = load_model('/content/drive/MyDrive/Colab Notebooks/Curso_IA_BIGDATA/TFM/export_models/Gredient_Boosted_TensowFlow/model_bg_limit', compile = False)
model_bg_less_limit = load_model('/content/drive/MyDrive/Colab Notebooks/Curso_IA_BIGDATA/TFM/export_models/Gredient_Boosted_TensowFlow/model_bg_less_limit', compile = False)
model_bg_less_columns = load_model('/content/drive/MyDrive/Colab Notebooks/Curso_IA_BIGDATA/TFM/export_models/Gredient_Boosted_TensowFlow/model_bg_less_columns', compile = False)

# Cargo los modelos en una lista
models_bg = [model_bg_complete, model_bg_limit, model_bg_less_limit, model_bg_less_columns]

Modelos de Random Forest - TensorFlow

In [55]:
model_rf_complete = load_model('/content/drive/MyDrive/Colab Notebooks/Curso_IA_BIGDATA/TFM/export_models/Random_forest_TensorFlow/model_rf_complete', compile = False)
model_rf_limit = load_model('/content/drive/MyDrive/Colab Notebooks/Curso_IA_BIGDATA/TFM/export_models/Random_forest_TensorFlow/model_rf_limit', compile = False)
model_rf_less_limit = load_model('/content/drive/MyDrive/Colab Notebooks/Curso_IA_BIGDATA/TFM/export_models/Random_forest_TensorFlow/model_rf_less_limit', compile = False)
model_rf_less_columns = load_model('/content/drive/MyDrive/Colab Notebooks/Curso_IA_BIGDATA/TFM/export_models/Random_forest_TensorFlow/model_rf_less_columns', compile = False)

# Cargo los modelos en una lista
models_rf = [model_rf_complete, model_rf_limit, model_rf_less_limit, model_rf_less_columns]

Creo una función para poder sacar los coeficientes de cada modelo

In [123]:
def grafic_predicction(real_values, predicted_values, r2, mse):
  fig = go.Figure()

  fig.update_layout(
      xaxis_title="Precio Predicho",
      yaxis_title="Precio Real",
      title={
          'text': "Predicción y rendimiento (R2 Score = {:.2f})".format(r2) + "(Absolute Error = {:.2f})".format(mse),
          'y':0.95,
          'x':0.5,
          'xanchor': 'center',
          'yanchor': 'top'})

  fig.add_trace(go.Scatter(x=real_values, y=predicted_values, 
                          mode='markers', 
                          marker=dict(size=5, color='#34495E', 
                                      line=dict(width=0.5, color='#196F3D')),
                          name='Precio'))

  # Calcular la línea de tendencia utilizando scipy.stats.linregress()
  slope, intercept, r_value, p_value, std_err = stats.linregress(real_values, predicted_values)
  trendline_x = [min(real_values), max(real_values)]
  trendline_y = [slope*xi + intercept for xi in trendline_x]

  # Añadir la línea de tendencia a la figura
  fig.add_trace(go.Scatter(x=trendline_x, y=trendline_y, 
                          mode='lines', 
                          line=dict(width=2, color='orange'), 
                          name='Tendencia'))


  fig.show()

In [124]:
def rendimiento_tensorflow(name_model ,input_model, input_test, imput_test_df):
    predicted_values = input_model.predict(imput_test_df)
    predicted_values = predicted_values.flatten()
    real_values = input_test[target].to_numpy()

    # Error Cuadrativo
    print("Error cuadrático medio: %.2f" % mean_squared_error(real_values, predicted_values, squared=False))
    # Coeficiente de determinación
    print(f"Coeficiente de determinación para '{name_model}': %.2f" % r2_score(real_values, predicted_values))

    mse = mean_squared_error(real_values, predicted_values, squared=False)
    r2 = r2_score(real_values, predicted_values)

    for i in range(10):
      real_price = real_values[i]
      estim_price = predicted_values[i]
      error_abs = abs(real_price - estim_price)
      print(f"{real_price:6.2f} {estim_price:12.2f} {error_abs:16.2f}")
    
    grafic_predicction(real_values, predicted_values, r2, mse)   

In [58]:
list_keys = list(dict_tr_ts.keys())

#### Predicciones con el conjunto de test guardados previamente en `dict_tr_ts`

Para los modelos de Gradient Boosted

In [127]:
for index, model in enumerate(list_keys):
  rendimiento_tensorflow(list_keys[index] ,models_bg[index], dict_tr_ts[model][0], dict_tr_ts[model][1])  
  time.sleep(5)

36/36 [==============================] - 1s 29ms/step
Error cuadrático medio: 12093.21
Coeficiente de determinación para 'complete': 0.86
10890.00     12174.65          1284.65
23490.00     21817.99          1672.01
37800.00     35141.57          2658.43
23500.00     22326.94          1173.06
12430.00     14483.66          2053.66
9020.00     11132.07          2112.07
23890.00     26358.06          2468.06
11299.00     12262.75           963.75
31000.00     28375.96          2624.04
53000.00     54085.22          1085.22


36/36 [==============================] - 1s 35ms/step
Error cuadrático medio: 1861.69
Coeficiente de determinación para 'limit': 0.97
21885.00     20409.21          1475.79
34890.00     33499.27          1390.73
20500.00     22666.50          2166.50
17990.00     18296.10           306.10
5400.00      5875.70           475.70
23920.00     22492.96          1427.04
15500.00     18398.94          2898.94
22990.00     19291.74          3698.26
10890.00     11104.05           214.05
29990.00     30072.15            82.15


36/36 [==============================] - 2s 50ms/step
Error cuadrático medio: 1801.79
Coeficiente de determinación para 'less_limit': 0.97
1250.00      1438.20           188.20
12496.00     12886.40           390.40
17940.00     16918.94          1021.06
29900.00     29530.64           369.36
11990.00     10570.65          1419.35
11385.00     11062.55           322.45
51490.00     56852.95          5362.95
2990.00      3271.54           281.54
10780.00     10527.30           252.70
16200.00     16584.78           384.78


36/36 [==============================] - 1s 33ms/step
Error cuadrático medio: 1827.12
Coeficiente de determinación para 'less_columns': 0.97
1250.00      1808.44           558.44
12496.00     12731.82           235.82
17940.00     17276.38           663.62
29900.00     29678.43           221.57
11990.00     10491.11          1498.89
11385.00     11012.06           372.94
51490.00     58499.55          7009.55
2990.00      3353.03           363.03
10780.00     10599.34           180.66
16200.00     16511.53           311.53


Para los modelos de RandomForest

In [128]:
for index, model in enumerate(list_keys):
  rendimiento_tensorflow(list_keys[index] ,models_rf[index], dict_tr_ts[model][0], dict_tr_ts[model][1])  
  time.sleep(5)

36/36 [==============================] - 1s 39ms/step
Error cuadrático medio: 12003.32
Coeficiente de determinación para 'complete': 0.86
10890.00     10582.84           307.16
23490.00     20455.77          3034.23
37800.00     33001.91          4798.09
23500.00     23011.21           488.79
12430.00     14112.73          1682.73
9020.00      9426.64           406.64
23890.00     26791.36          2901.36
11299.00     11136.65           162.35
31000.00     27781.61          3218.39
53000.00     53985.16           985.16


36/36 [==============================] - 1s 28ms/step
Error cuadrático medio: 2823.97
Coeficiente de determinación para 'limit': 0.94
21885.00     17558.68          4326.32
34890.00     33694.29          1195.71
20500.00     23288.17          2788.17
17990.00     19223.36          1233.36
5400.00      8405.61          3005.61
23920.00     22514.79          1405.21
15500.00     15908.40           408.40
22990.00     18598.11          4391.89
10890.00     11531.50           641.50
29990.00     28807.09          1182.91


36/36 [==============================] - 2s 52ms/step
Error cuadrático medio: 2813.75
Coeficiente de determinación para 'less_limit': 0.94
1250.00      2910.87          1660.87
12496.00     13354.40           858.40
17940.00     17641.89           298.11
29900.00     28136.81          1763.19
11990.00     11674.43           315.57
11385.00     10995.50           389.50
51490.00     57793.87          6303.87
2990.00      5072.04          2082.04
10780.00     10247.39           532.61
16200.00     16509.24           309.24


36/36 [==============================] - 1s 34ms/step
Error cuadrático medio: 2792.48
Coeficiente de determinación para 'less_columns': 0.94
1250.00      3248.42          1998.42
12496.00     13270.25           774.25
17940.00     17669.58           270.42
29900.00     28442.10          1457.90
11990.00     11316.62           673.38
11385.00     10830.09           554.91
51490.00     58043.61          6553.61
2990.00      4893.38          1903.38
10780.00     10123.59           656.41
16200.00     16713.47           513.47


Por último visualizo los arboles de decisión

In [61]:
# tfdf.model_plotter.plot_model_in_colab(model_car_GB)

#### Predicciones TensorFlow con coche externo

Referencia de la marca de coche que vamos a predecir

In [67]:
dict_tr_ts['less_columns'][0][dict_tr_ts['less_columns'][0]['car_brand'] == 'Saab']

car_brand     model    year  horses        km      fuel gearbox  \
173184      Saab  Saab 9-3  2007.0   150.0  270000.0    Diesel  Manual   
59424       Saab  Saab 9-3  2006.0   175.0  114378.0  Gasolina  Manual   
24172       Saab  Saab 9-3  2006.0   150.0  200000.0    Diesel  Manual   
116728      Saab  Saab 9-3  2006.0   175.0  114378.0  Gasolina  Manual   
148358      Saab  Saab 9-3  2006.0   175.0  114378.0  Gasolina  Manual   
11764       Saab  Saab 9-3  2006.0   175.0  114378.0  Gasolina  Manual   
112518      Saab  Saab 9-5  1999.0   150.0  149000.0  Gasolina  Manual   
113438      Saab  Saab 9-3  2006.0   175.0  114378.0  Gasolina  Manual   

         price  displ_engine  marches  
173184  3500.0        1910.0      6.0  
59424   5900.0        1998.0      5.0  
24172   4600.0        1910.0      6.0  
116728  5900.0        1998.0      5.0  
148358  5900.0        1998.0      5.0  
11764   5900.0        1998.0      5.0  
112518  2990.0        1985.0      5.0  
113438  5900.0        1998.0      5.0

#### Realizando predicción con un coche externo

In [62]:
# Test
car_predict = pd.Series(data={'car_brand': 'Saab',	'model':	'Saab 9-3', 'year': 2005.0,	'horses': 150.0, 'km': 190000.0, 'fuel': 'Diesel',	'gearbox': 'Manual', 'price': 0.0, 'displ_engine': 1910.0, 'marches': 6.0})
new_car = pd.DataFrame([car_predict])
new_car_df = tfdf.keras.pd_dataframe_to_tf_dataset(new_car, label='price', task=tfdf.keras.Task.REGRESSION)

In [63]:
price_car_full = model_bg_less_columns.predict(new_car_df)
price_car_full

1/1 [==============================] - 0s 29ms/step


array([[4761.1543]], dtype=float32)

###  Machine Learning - Sklearn

In [74]:
dict_sklearn = {}

for index, df in enumerate(dict_dataframes['sklearn']):
  X = dict_dataframes['sklearn'][df].drop(['price'], axis = 1)
  y = dict_dataframes['sklearn'][df]['price']

  X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.20)

  dict_sklearn.update({df:[X_test, y_test]})

  rf_model = RandomForestRegressor().fit(X_train.values, y_train.values)
  print(f'Proceso de entrenamiento completado de {df}')

  joblib.dump(rf_model, f'/content/drive/MyDrive/Colab Notebooks/Curso_IA_BIGDATA/TFM/export_models/Sklearn_RF/Sklearn_RF_{df}.pkl', compress=9)
  print(f'Proceso de exportación de Sklearn_RF_{df} completado')  

Proceso de entrenamiento completado
Proceso de exportación completado
Proceso de entrenamiento completado
Proceso de exportación completado
Proceso de entrenamiento completado
Proceso de exportación completado
Proceso de entrenamiento completado
Proceso de exportación completado


Modelos Sklearn RandomForest

In [75]:
rf_sk_complete = joblib.load('/content/drive/MyDrive/Colab Notebooks/Curso_IA_BIGDATA/TFM/export_models/Sklearn_RF/Sklearn_RF_complete.pkl')
rf_sk_limit = joblib.load('/content/drive/MyDrive/Colab Notebooks/Curso_IA_BIGDATA/TFM/export_models/Sklearn_RF/Sklearn_RF_limit.pkl')
rf_sk_less_limit = joblib.load('/content/drive/MyDrive/Colab Notebooks/Curso_IA_BIGDATA/TFM/export_models/Sklearn_RF/Sklearn_RF_less_limit.pkl')
rf_sk_less_columns = joblib.load('/content/drive/MyDrive/Colab Notebooks/Curso_IA_BIGDATA/TFM/export_models/Sklearn_RF/Sklearn_RF_less_columns.pkl')

models_sklearn_rf = [rf_sk_complete, rf_sk_limit, rf_sk_less_limit, rf_sk_less_columns]

In [125]:
def rendimiento_sklearn(name_model ,input_model, input_test, imput_test_df):
    # Predicción con las entradas de test
    predicted_values = input_model.predict(input_test.values)
    # Saco los valores reales de test
    real_values = imput_test_df.values

    # Error Cuadrativo
    print("Error cuadrático medio: %.2f" % mean_squared_error(real_values, predicted_values, squared=False))
    # Coeficiente de determinación
    print(f"Coeficiente de determinación para '{name_model}': %.2f" % r2_score(real_values, predicted_values))
    
    # Saco predicciones
    print('Sacando predicciones')
    for i in range(10):
      real_price = real_values[i]
      estim_price = predicted_values[i]
      error_abs = abs(real_price - estim_price)
      print(f"{real_price:6.2f} {estim_price:12.2f} {error_abs:16.2f}")
    print('\n')

    # r2_score y mean_squared_error nos permite saber el rendimiento del modelo
    r2 = r2_score(real_values, predicted_values)
    mse = mean_squared_error(real_values, predicted_values, squared=False)
    
    # Dibujo una gráfica con los resultados
    grafic_predicction(real_values, predicted_values, r2, mse)   

#### Predicciones con el conjunto de test guardados previamente en `dict_sklearn`

In [131]:
for index, model in enumerate(list_keys):
  rendimiento_sklearn(list_keys[index], models_sklearn_rf[index], dict_sklearn[model][0], dict_sklearn[model][1])  
  time.sleep(5)

Error cuadrático medio: 8791.71
Coeficiente de determinación para 'complete': 0.92
Sacando predicciones
72880.00     61211.61         11668.39
20499.00     20378.15           120.85
9400.00      9407.98             7.98
41500.00     41566.38            66.38
26335.00     26335.00             0.00
28175.00     28175.00             0.00
12900.00     11923.77           976.23
18999.00     19159.70           160.70
22900.00     22605.17           294.83
10590.00     10626.70            36.70




Error cuadrático medio: 1706.74
Coeficiente de determinación para 'limit': 0.98
Sacando predicciones
23900.00     23866.90            33.10
8500.00      7784.77           715.23
20125.00     20145.65            20.65
16170.00     16170.00             0.00
27990.00     28449.62           459.62
15900.00     16710.76           810.76
12990.00     12990.00             0.00
20470.00     20449.50            20.50
17490.00     16921.93           568.07
53990.00     53365.59           624.41




Error cuadrático medio: 1660.32
Coeficiente de determinación para 'less_limit': 0.98
Sacando predicciones
37995.00     38004.05             9.05
15490.00     15414.02            75.98
28990.00     29023.30            33.30
29555.00     29552.70             2.30
27490.00     28098.10           608.10
33990.00     33726.40           263.60
18258.00     18244.42            13.58
37995.00     36389.69          1605.31
16900.00     17168.68           268.68
41450.00     39999.33          1450.67




Error cuadrático medio: 1804.16
Coeficiente de determinación para 'less_columns': 0.97
Sacando predicciones
15990.00     15840.39           149.61
21000.00     21000.00             0.00
18990.00     18749.80           240.20
25500.00     25189.58           310.42
12500.00     12500.00             0.00
8799.00      8765.52            33.48
18950.00     17425.14          1524.86
8899.00      8961.82            62.82
14190.00     14190.00             0.00
14350.00     14350.00             0.00




In [133]:
dict_sklearn['less_columns'][0]

year  horses        km  displ_engine  marches  card_brand_id  \
130022  2016.0   115.0   72601.0        1197.0      6.0           49.0   
17631   2004.0   400.0   79000.0        4244.0      6.0           40.0   
56575   2018.0   132.0   66000.0        1591.0      6.0           31.0   
64699   2022.0   125.0      10.0         999.0      6.0           20.0   
38085   2010.0   126.0   25228.0        1998.0      6.0           67.0   
...        ...     ...       ...           ...      ...            ...   
169983  2018.0   120.0   80921.0         998.0      6.0           24.0   
36809   2015.0   105.0  178111.0        1598.0      6.0            1.0   
168056  2018.0   130.0   73258.0        1598.0      6.0           49.0   
166444  2003.0    61.0   62000.0        1124.0      5.0           10.0   
41653   2019.0   110.0   59542.0        1598.0      6.0           50.0   

        model_id  fuel_id  gearbox_id  
130022     476.0      3.0         1.0  
17631      383.0      3.0         0.0  
56575      327.0      3.0         1.0  
64699      219.0      3.0         1.0  
38085      664.0      1.0         1.0  
...          ...      ...         ...  
169983     266.0      3.0         1.0  
36809       12.0      1.0         1.0  
168056     479.0      1.0         1.0  
166444     117.0      3.0         1.0  
41653      484.0      1.0         1.0  

[35299 rows x 9 columns]

#### Predicciones Sklearn con coche externo

Vamos a usar el mismo vehículo pero cambiando los datos por numericos, ya que el Random Forest de Sklearn no puede trabajar con valores categoricos, solo con numericos

Los datos del coche son los siguientes:

`{'car_brand': 'Saab',	'model':	'Saab 9-3', 'year': 2005.0,	'horses': 150.0, 'km': 190000.0, 'fuel': 'Diesel',	'gearbox': 'Manual', 'price': 0.0, 'displ_engine': 1910.0, 'marches': 6.0}` 

Que para sklearn quedarian de la siguiente manera:

`[2005.0, 150.0, 190000.0, 1910.0, 6.0, 57.0, 1, 1]`

In [140]:
dict_sklearn['less_columns'][0][dict_sklearn['less_columns'][0]['card_brand_id'] == 57.0]

year  horses        km  displ_engine  marches  card_brand_id  \
59424   2006.0   175.0  114378.0        1998.0      5.0           57.0   
122953  2004.0   150.0  313000.0        1988.0      5.0           57.0   
24172   2006.0   150.0  200000.0        1910.0      6.0           57.0   
57616   1995.0   150.0   48000.0        2290.0      5.0           57.0   
35402   2005.0   210.0  215000.0        1998.0      5.0           57.0   
82213   2000.0   150.0  160656.0        1985.0      5.0           57.0   
146191  2006.0   175.0  114378.0        1998.0      5.0           57.0   
116728  2006.0   175.0  114378.0        1998.0      5.0           57.0   
173184  2007.0   150.0  270000.0        1910.0      6.0           57.0   
148358  2006.0   175.0  114378.0        1998.0      5.0           57.0   
169091  2006.0   150.0  270000.0        1910.0      6.0           57.0   

        model_id  fuel_id  gearbox_id  
59424      575.0      3.0         1.0  
122953     575.0      3.0         1.0  
24172      575.0      1.0         1.0  
57616      577.0      3.0         1.0  
35402      575.0      3.0         1.0  
82213      576.0      3.0         1.0  
146191     575.0      3.0         1.0  
116728     575.0      3.0         1.0  
173184     575.0      1.0         1.0  
148358     575.0      3.0         1.0  
169091     575.0      1.0         0.0

In [146]:
new_car = rf_sk_less_columns.predict([[2005.0, 150.0, 190000.0, 1910.0, 6.0, 57.0, 575.0, 1, 1]])
new_car

array([5831.82])